## Import Libraries

In [77]:
import numpy as np
import pandas as pd
import scipy 
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline
import plotly.express as px
import warnings
warnings.filterwarnings('ignore')
import plotly.figure_factory as ff
import unicodedata
from sklearn.preprocessing import StandardScaler
import os
from tqdm.auto import tqdm
from sklearn.metrics import r2_score
from sklearn.model_selection import train_test_split
from sklearn.linear_model import Lasso
from sklearn.linear_model import Ridge
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import ElasticNet
plt.style.use('dark_background')
import statsmodels.api as sm 
import plotly.io as pio
pio.templates.default = "plotly_dark"
from scipy import stats

## Loading Data 

In [78]:
data=pd.read_csv('/kaggle/input/life-expectancy-who/Life Expectancy Data.csv')

In [79]:
data

Country  Year      Status  Life expectancy   Adult Mortality  \
0     Afghanistan  2015  Developing              65.0            263.0   
1     Afghanistan  2014  Developing              59.9            271.0   
2     Afghanistan  2013  Developing              59.9            268.0   
3     Afghanistan  2012  Developing              59.5            272.0   
4     Afghanistan  2011  Developing              59.2            275.0   
...           ...   ...         ...               ...              ...   
2933     Zimbabwe  2004  Developing              44.3            723.0   
2934     Zimbabwe  2003  Developing              44.5            715.0   
2935     Zimbabwe  2002  Developing              44.8             73.0   
2936     Zimbabwe  2001  Developing              45.3            686.0   
2937     Zimbabwe  2000  Developing              46.0            665.0   

      infant deaths  Alcohol  percentage expenditure  Hepatitis B  Measles   \
0                62     0.01               71.279624         65.0      1154   
1                64     0.01               73.523582         62.0       492   
2                66     0.01               73.219243         64.0       430   
3                69     0.01               78.184215         67.0      2787   
4                71     0.01                7.097109         68.0      3013   
...             ...      ...                     ...          ...       ...   
2933             27     4.36                0.000000         68.0        31   
2934             26     4.06                0.000000          7.0       998   
2935             25     4.43                0.000000         73.0       304   
2936             25     1.72                0.000000         76.0       529   
2937             24     1.68                0.000000         79.0      1483   

      ...  Polio  Total expenditure  Diphtheria    HIV/AIDS         GDP  \
0     ...    6.0               8.16         65.0        0.1  584.259210   
1     ...   58.0               8.18         62.0        0.1  612.696514   
2     ...   62.0               8.13         64.0        0.1  631.744976   
3     ...   67.0               8.52         67.0        0.1  669.959000   
4     ...   68.0               7.87         68.0        0.1   63.537231   
...   ...    ...                ...          ...        ...         ...   
2933  ...   67.0               7.13         65.0       33.6  454.366654   
2934  ...    7.0               6.52         68.0       36.7  453.351155   
2935  ...   73.0               6.53         71.0       39.8   57.348340   
2936  ...   76.0               6.16         75.0       42.1  548.587312   
2937  ...   78.0               7.10         78.0       43.5  547.358878   

      Population   thinness  1-19 years   thinness 5-9 years  \
0     33736494.0                   17.2                 17.3   
1       327582.0                   17.5                 17.5   
2     31731688.0                   17.7                 17.7   
3      3696958.0                   17.9                 18.0   
4      2978599.0                   18.2                 18.2   
...          ...                    ...                  ...   
2933  12777511.0                    9.4                  9.4   
2934  12633897.0                    9.8                  9.9   
2935    125525.0                    1.2                  1.3   
2936  12366165.0                    1.6                  1.7   
2937  12222251.0                   11.0                 11.2   

      Income composition of resources  Schooling  
0                               0.479       10.1  
1                               0.476       10.0  
2                               0.470        9.9  
3                               0.463        9.8  
4                               0.454        9.5  
...                               ...        ...  
2933                            0.407        9.2  
2934                            0.418        9.5  
2935                            0.427      

In [80]:
data.isnull().sum()

Country                              0
Year                                 0
Status                               0
Life expectancy                     10
Adult Mortality                     10
infant deaths                        0
Alcohol                            194
percentage expenditure               0
Hepatitis B                        553
Measles                              0
 BMI                                34
under-five deaths                    0
Polio                               19
Total expenditure                  226
Diphtheria                          19
 HIV/AIDS                            0
GDP                                448
Population                         652
 thinness  1-19 years               34
 thinness 5-9 years                 34
Income composition of resources    167
Schooling                          163
dtype: int64

In [81]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2938 entries, 0 to 2937
Data columns (total 22 columns):
 #   Column                           Non-Null Count  Dtype  
---  ------                           --------------  -----  
 0   Country                          2938 non-null   object 
 1   Year                             2938 non-null   int64  
 2   Status                           2938 non-null   object 
 3   Life expectancy                  2928 non-null   float64
 4   Adult Mortality                  2928 non-null   float64
 5   infant deaths                    2938 non-null   int64  
 6   Alcohol                          2744 non-null   float64
 7   percentage expenditure           2938 non-null   float64
 8   Hepatitis B                      2385 non-null   float64
 9   Measles                          2938 non-null   int64  
 10   BMI                             2904 non-null   float64
 11  under-five deaths                2938 non-null   int64  
 12  Polio               

## Imputing Missing Values

In [82]:
data['Life expectancy ']=data['Life expectancy '].fillna(value=data['Life expectancy '].mean())
data['Adult Mortality']=data['Adult Mortality'].fillna(value=data['Adult Mortality'].mean())


In [83]:
px.scatter(data,x='Schooling',y='Alcohol',color='Country', size ='Life expectancy ', template='plotly_dark',title='<b> Schooling vs Alcohol')

In [84]:
# These values are mean values of the selected interval of other feature.

def impute_Alcohol(cols):
    al=cols[0]
    sc=cols[1]
    if pd.isnull(al):
        if sc<=2.5:
            return 4.0
        elif 2.5<sc<=5.0:
            return 1.5
        elif 5.0<sc<=7.5:
            return 2.5
        elif 7.5<sc<=10.0:
            return 3.0
        elif 10.0<sc<=15:
            return 4.0
        elif sc>15:
            return 10.0
    else:
        return al
    
data['Alcohol']=data[['Alcohol','Schooling']].apply(impute_Alcohol,axis=1)
data['Alcohol']=data['Alcohol'].fillna(value=data['Alcohol'].mean())

In [85]:
fig = ff.create_distplot([data['Alcohol']], group_labels = ['Alcohol'])
fig.show()

In [86]:
scipy.stats.skew(data['Alcohol'],axis=0)

# This shows that this column has positive skew.

0.5964252568271263

In [87]:
px.scatter(data,x='Life expectancy ',y='Polio',color='Country', template='plotly_dark',title='<b> Polio vs Life Expectancy')

We impute 'Polio' in the same manner we did for 'Alcohol'

In [88]:
def impute_polio(c):
    p=c[0]
    l=c[1]
    if pd.isnull(p):
        if l<=45:
            return 80.0
        elif 45<l<=50:
            return 67.0
        elif 50<l<=60:
            return 87.44
        elif 60<l<=70:
            return 91
        elif 70<l<=80:
            return 94.3
        elif l>80:
            return 95
    else:
        return p
    
data['Polio']=data[['Polio','Life expectancy ']].apply(impute_polio,axis=1)

Now we impute 'Diptheria' with 'Polio' 

In [89]:
px.scatter(data,x='Polio',y='Diphtheria ',color='Country', template='plotly_dark',title='<b> Polio vs Diphtheria')

In [90]:
def impute_Diptheria(c):
    d=c[0]
    p=c[1]
    if pd.isnull(d):
        if p<=10:
            return 75.0
        elif 10<p<=40:
            return 37.0
        elif 40<p<=45:
            return 40.0
        elif 45<p<=50:
            return 50.0
        elif 50<p<=60:
            return 55.0
        elif 60<p<=80:
            return 65.0
        elif p>80:
            return 90.0
    else:
        return d
data['Diphtheria ']=data[['Diphtheria ','Polio']].apply(impute_Diptheria,axis=1)

In [91]:
# We verify that Diphtheria, Polio have no NaN values

a=list(data.columns)
b=[]
for i in a:
    c=data[i].isnull().sum()
    b.append(c)
null_df=pd.DataFrame({'Feature name':a,'no. of Nan':b})
null_df


Feature name  no. of Nan
0                           Country           0
1                              Year           0
2                            Status           0
3                  Life expectancy            0
4                   Adult Mortality           0
5                     infant deaths           0
6                           Alcohol           0
7            percentage expenditure           0
8                       Hepatitis B         553
9                          Measles            0
10                             BMI           34
11               under-five deaths            0
12                            Polio           0
13                Total expenditure         226
14                      Diphtheria            0
15                         HIV/AIDS           0
16                              GDP         448
17                       Population         652
18             thinness  1-19 years          34
19               thinness 5-9 years          34
20  Income composition of resources         167
21                        Schooling         163

Now using 'Diphtheria' we impute 'Hepatitis B'

In [92]:
def impute_HepatatisB(cols):
    hep=cols[0]
    dip=cols[1]
    if pd.isnull(hep):
        if dip<=15:
            return 75.0
        elif 15<dip<=30:
            return 20.0
        elif 30<dip<=45:
            return 38.0
        elif 45<dip<=60:
            return 43.0
        elif 60<dip<=80:
            return 63.0
        elif dip>80:
            return 88.4
    else:
        return hep
    
data['Hepatitis B']=data[['Hepatitis B','Diphtheria ']].apply(impute_HepatatisB,axis=1)

In [93]:
data['Diphtheria '].isnull().sum()

0

In [94]:
px.scatter(data,x='Life expectancy ',y=' BMI ',color='Country', template='plotly_dark',title='<b> Life Expectancy vs BMI')

In [95]:
def impute_BMI(c):
    b=c[0]
    l=c[1]
    if pd.isnull(b):
        if l<=50:
            return 25.0
        elif 50<l<=60:
            return 25.0
        elif 60<l<=70:
            return 32.0
        elif 70<l<=80:
            return 46.8
        elif 80<l<=100:
            return 60.0
    else:
        return b
    
data[' BMI ']=data[[' BMI ','Life expectancy ']].apply(impute_BMI,axis=1)


In [96]:
px.scatter(data,x='Alcohol',y='Total expenditure',color='Country', template='plotly_dark',title='<b> Alcohol vs Total Expenditure')

In [97]:
def impute_Total_exp(c):
    t=c[0]
    a=c[1]
    if pd.isnull(t):
        if a<=2.5:
            return 5.08
        elif 2.5<a<=5.0:
            return 6.0
        elif 5.0<a<=10.0:
            return 6.71
        elif 10.0<a<=12.5:
            return 6.9
        elif a>12.5:
            return 6.68
    else:
        return t
    
data['Total expenditure']=data[['Total expenditure','Alcohol']].apply(impute_Total_exp,axis=1)        


In [98]:
px.scatter(data,x='percentage expenditure',y='GDP',color='Country', template='plotly_dark',title='<b> Percentage Expenditure vs GDP')

In [99]:
def impute_GDP(c):
    g=c[0]
    p=c[1]
    if pd.isnull(g):
        if p<=1250:
            return 1100.0
        elif 1250<p<=2500:
            return 1800.0
        elif 2500<p<=3750:
            return 2900.0
        elif 3750<p<=7500:
            return 3500.0
        elif 7500<p<=8750:
            return 4500.0
        elif 8750<p<=10000:
            return 5000.0
        elif 10000<p<=11250:
            return 5700.0
        elif 11250<p<=12500:
            return 7000.0
        elif 12500<p<=15000:
            return 8000.0
        elif 15000<p<=17500:
            return 9000.0
        elif p>17500:
            return 8500.0
    else:
        return g
    
data['GDP']=data[['GDP','percentage expenditure']].apply(impute_GDP,axis=1)

In [100]:
px.scatter(data,x='infant deaths',y='Population',color='Country', template='plotly_dark',title='<b> Infant Deaths vs Population')

In [101]:
def impute_population(c):
    p=c[0]
    i=c[1]
    if pd.isnull(p):
        if i<=100:
            return 0.19*((10)**9)
        elif 100<i<=250:
            return 0.18*((10)**9)
        elif 250<i<=350:
            return 0.02*((10)**9)
        elif 350<i<=900:
            return 0.1*((10)**9)
        elif 900<i<=1100:
            return 0.18*((10)**9)
        elif 1100<i<=1250:
            return 0.05*((10)**9)
        elif 1250<i<=1500:
            return 0.19*((10)**9)
        elif 1500<i<=1750:
            return 0.05*((10)**9)
        elif i>1750:
            return 0.1*((10)**9)
    else:
        return p
    
data['Population']=data[['Population','infant deaths']].apply(impute_population,axis=1)

In [102]:
px.scatter(data,x=' BMI ',y=' thinness  1-19 years',color='Country', template='plotly_dark',title='<b> BMI vs Thinness 1-19 years')

In [103]:
def impute_Thin_1(c):
    t=c[0]
    b=c[1]
    if pd.isnull(t):
        if b<=10:
            return 5.0
        elif 10<b<=20:
            return 10.0
        elif 20<b<=30:
            return 8.0
        elif 30<b<=40:
            return 6.0
        elif 40<b<=50:
            return 3.0
        elif 50<b<=70:
            return 4.0
        elif b>70:
            return 1.0
    else:
        return t
    
data[' thinness  1-19 years']=data[[' thinness  1-19 years',' BMI ']].apply(impute_Thin_1,axis=1)

In [104]:
px.scatter(data,x=' BMI ',y= ' thinness 5-9 years',color='Country', template='plotly_dark',title='<b> BMI vs Thinness 5-9 years')

In [105]:
def impute_Thin_2(c):
    t=c[0]
    b=c[1]
    if pd.isnull(t):
        if b<=10:
            return 5.0
        elif 10<b<=20:
            return 10.0
        elif 20<b<=30:
            return 8.0
        elif 30<b<=40:
            return 6.0
        elif 40<b<=50:
            return 3.0
        elif 50<b<=70:
            return 4.0
        elif b>70:
            return 1.0
    else:
        return t
    
data[' thinness 5-9 years']=data[[' thinness 5-9 years',' BMI ']].apply(impute_Thin_2,axis=1)

In [106]:
px.scatter(data,x='Life expectancy ',y= 'Income composition of resources',color='Country', template='plotly_dark',title='<b> Life Expectancy vs Income Composition of Resources')

In [107]:
def impute_Income(c):
    i=c[0]
    l=c[1]
    if pd.isnull(i):
        if l<=40:
            return 0.4
        elif 40<l<=50:
            return 0.42
        elif 50<l<=60:
            return 0.402
        elif 60<l<=70:
            return 0.54
        elif 70<l<=80:
            return 0.71
        elif l>80:
            return 0.88
    else:
        return i
        
data['Income composition of resources']=data[['Income composition of resources','Life expectancy ']].apply(impute_Income,axis=1)

In [108]:
px.scatter(data,x='Life expectancy ',y= 'Schooling',color='Country', template='plotly_dark',title='<b> Life Expectancy vs Schooling')

In [109]:
def impute_schooling(c):
    s=c[0]
    l=c[1]
    if pd.isnull(s):
        if l<= 40:
            return 8.0
        elif 40<l<=44:
            return 7.5
        elif 44<l<50:
            return 8.1
        elif 50<l<=60:
            return 8.2
        elif 60<l<=70:
            return 10.5
        elif 70<l<=80:
            return 13.4
        elif l>80:
            return 16.5
    else:
        return s
    
data['Schooling']=data[['Schooling','Life expectancy ']].apply(impute_schooling,axis=1)


In [110]:
a=list(data.columns)
b=[]
for i in a:
    c=data[i].isnull().sum()
    b.append(c)
null_df=pd.DataFrame({'Feature name':a,'no. of Nan':b})
null_df

Feature name  no. of Nan
0                           Country           0
1                              Year           0
2                            Status           0
3                  Life expectancy            0
4                   Adult Mortality           0
5                     infant deaths           0
6                           Alcohol           0
7            percentage expenditure           0
8                       Hepatitis B           0
9                          Measles            0
10                             BMI            0
11               under-five deaths            0
12                            Polio           0
13                Total expenditure           0
14                      Diphtheria            0
15                         HIV/AIDS           0
16                              GDP           0
17                       Population           0
18             thinness  1-19 years           0
19               thinness 5-9 years           0
20  Income composition of resources           0
21                        Schooling           0

## EDA

In [111]:
fig = ff.create_distplot([data['Life expectancy ']], group_labels = ['Life Expectancy'])
fig.show()

In [112]:
fig=px.histogram(data,x='Life expectancy ',template='plotly_dark')
fig.show()

Developed countries have maximum life expectancy

In [113]:
fig=px.violin(data,x='Status',y='Life expectancy ',color='Status',template='plotly_dark',box=True,title='Life expectancy Based on Countries status')
fig.show()


In [114]:
fig=px.line(data.sort_values(by='Year'),x='Year',y='Life expectancy ',animation_frame='Country',animation_group='Year',color='Country',markers=True,template='plotly_dark',title='<b> Country wise Life Expectancy over Years')
fig.show()

In [115]:
px.scatter(data,y='Adult Mortality',x='Life expectancy ',color='Country',size='Life expectancy ',template='plotly_dark',opacity=0.6,title='<b> Life Expectancy Versus Adult Mortality')

In [116]:
px.scatter(data,x='Life expectancy ',y='percentage expenditure',color='Country',size='Year',template='plotly_dark',title='<b> Life Expectancy Versus Percentage expenditure')

DECREASE IN INFANT DEATHS INCREASES LIFE EXPECTANCY

In [117]:
px.scatter(data.sort_values(by='Year'),y='infant deaths',x='Life expectancy ',template='plotly_dark',size='Year',color='Country',opacity=0.6,title='<b>Life Expectancy Versus Infant Deaths of Countries in every Year')

In [118]:
px.scatter_3d(data.sort_values(by='Year'),y='Schooling',x='Life expectancy ',z='Total expenditure',template='plotly_dark',color='Country',size='Total expenditure')

In [119]:
px.scatter_3d(data.sort_values(by='Year'),y='Adult Mortality',x='Life expectancy ',z='infant deaths',size='Life expectancy ',template='plotly_dark',color='Country')

In [120]:
px.scatter(data.sort_values(by='Year'),y='Schooling',x='Life expectancy ',animation_frame='Year',animation_group='Country',template='plotly_dark',color='Country',size='Life expectancy ',title='<b> Life expectancy versus Schooling of countries in every year')

In [121]:
px.scatter(data.sort_values(by='Year'),y='Adult Mortality',x='Life expectancy ',animation_frame='Year',animation_group='Country',color='Country',size='Life expectancy ',opacity=0.6,template='plotly_dark',title='<b> Life Expectancy Versus Adult Mortality in every year')

## Models

In [122]:
X = data.drop(['Life expectancy ', 'Country', 'Year'], axis = 1)
y = data['Life expectancy ']

In [123]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2938 entries, 0 to 2937
Data columns (total 19 columns):
 #   Column                           Non-Null Count  Dtype  
---  ------                           --------------  -----  
 0   Status                           2938 non-null   object 
 1   Adult Mortality                  2938 non-null   float64
 2   infant deaths                    2938 non-null   int64  
 3   Alcohol                          2938 non-null   float64
 4   percentage expenditure           2938 non-null   float64
 5   Hepatitis B                      2938 non-null   float64
 6   Measles                          2938 non-null   int64  
 7    BMI                             2938 non-null   float64
 8   under-five deaths                2938 non-null   int64  
 9   Polio                            2938 non-null   float64
 10  Total expenditure                2938 non-null   float64
 11  Diphtheria                       2938 non-null   float64
 12   HIV/AIDS           

In [124]:
# X['Country'].nunique()

In [125]:
X['Status'].unique()

array(['Developing', 'Developed'], dtype=object)

In [126]:
# Country_dummy=pd.get_dummies(X['Country']) # Dummy variables for Country feature.

In [127]:
X['Status'] = X['Status'].apply(lambda x: 1 if x == 'Developed' else 0)

In [128]:
# status_dummy=pd.get_dummies(X['Status']) # Dummy variables for status feature.


In [129]:
# #X.drop(['Status'],inplace=True,axis=1)
# X = pd.concat([X, status_dummy],axis=1)
X.head()

Status  Adult Mortality  infant deaths  Alcohol  percentage expenditure  \
0       0            263.0             62     0.01               71.279624   
1       0            271.0             64     0.01               73.523582   
2       0            268.0             66     0.01               73.219243   
3       0            272.0             69     0.01               78.184215   
4       0            275.0             71     0.01                7.097109   

   Hepatitis B  Measles    BMI   under-five deaths   Polio  Total expenditure  \
0         65.0      1154   19.1                  83    6.0               8.16   
1         62.0       492   18.6                  86   58.0               8.18   
2         64.0       430   18.1                  89   62.0               8.13   
3         67.0      2787   17.6                  93   67.0               8.52   
4         68.0      3013   17.2                  97   68.0               7.87   

   Diphtheria    HIV/AIDS         GDP  Population   thinness  1-19 years  \
0         65.0        0.1  584.259210  33736494.0                   17.2   
1         62.0        0.1  612.696514    327582.0                   17.5   
2         64.0        0.1  631.744976  31731688.0                   17.7   
3         67.0        0.1  669.959000   3696958.0                   17.9   
4         68.0        0.1   63.537231   2978599.0                   18.2   

    thinness 5-9 years  Income composition of resources  Schooling  
0                 17.3                            0.479       10.1  
1                 17.5                            0.476       10.0  
2                 17.7                            0.470        9.9  
3                 18.0                            0.463        9.8  
4                 18.2                            0.454        9.5

In [130]:
X.shape

(2938, 19)

In [131]:
cols = X.columns

In [132]:
X = StandardScaler().fit_transform(X)

In [133]:
X = pd.DataFrame(X, columns = cols)

In [134]:
X = sm.add_constant(X) 
X.head()

const    Status  Adult Mortality  infant deaths   Alcohol  \
0    1.0 -0.459399         0.791586       0.268824 -1.162905   
1    1.0 -0.459399         0.856072       0.285786 -1.162905   
2    1.0 -0.459399         0.831890       0.302749 -1.162905   
3    1.0 -0.459399         0.864132       0.328193 -1.162905   
4    1.0 -0.459399         0.888314       0.345155 -1.162905   

   percentage expenditure  Hepatitis B  Measles      BMI   under-five deaths   \
0               -0.335570    -0.587067 -0.110384 -0.95681            0.255359   
1               -0.334441    -0.709594 -0.168124 -0.98186            0.274060   
2               -0.334594    -0.627909 -0.173531 -1.00691            0.292761   
3               -0.332096    -0.505382  0.032045 -1.03196            0.317696   
4               -0.367862    -0.464539  0.051757 -1.05200            0.342631   

      Polio  Total expenditure  Diphtheria    HIV/AIDS       GDP  Population  \
0 -3.278388           0.922074    -0.733975  -0.323445 -0.444412   -0.200665   
1 -1.052325           0.930397    -0.860838  -0.323445 -0.442279   -0.567337   
2 -0.881089           0.909590    -0.776262  -0.323445 -0.440850   -0.222668   
3 -0.667044           1.071880    -0.649399  -0.323445 -0.437984   -0.530357   
4 -0.624235           0.801397    -0.607112  -0.323445 -0.483465   -0.538241   

    thinness  1-19 years   thinness 5-9 years  \
0               2.801270             2.762027   
1               2.869414             2.806568   
2               2.914842             2.851108   
3               2.960271             2.917919   
4               3.028414             2.962460   

   Income composition of resources  Schooling  
0                        -0.698698  -0.554154  
1                        -0.713079  -0.584141  
2                        -0.741840  -0.614128  
3                        -0.775395  -0.644115  
4                        -0.818537  -0.734075

In [135]:
#X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=90)

In [136]:
X_transpose_X = np.dot(np.transpose(X),X)
X_trans_X_inv = np.linalg.inv(X_transpose_X)
b_cap = np.matmul(X_trans_X_inv, X.T) @ y

In [137]:
est=sm.OLS(y,X).fit() 
est.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:       Life expectancy    R-squared:                       0.836
Model:                            OLS   Adj. R-squared:                  0.835
Method:                 Least Squares   F-statistic:                     781.8
Date:                Wed, 20 Sep 2023   Prob (F-statistic):               0.00
Time:                        02:45:22   Log-Likelihood:                -8130.9
No. Observations:                2938   AIC:                         1.630e+04
Df Residuals:                    2918   BIC:                         1.642e+04
Df Model:                          19                                         
Covariance Type:            nonrobust                                         
===================================================================================================
                                      coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------------------------------------------
const                              69.2249      0.071    970.824      0.000      69.085      69.365
Status                              0.4807      0.098      4.886      0.000       0.288       0.674
Adult Mortality                    -2.1819      0.095    -22.900      0.000      -2.369      -1.995
infant deaths                      11.0007      0.936     11.754      0.000       9.166      12.836
Alcohol                             0.0746      0.099      0.750      0.453      -0.120       0.270
percentage expenditure              0.2420      0.172      1.407      0.159      -0.095       0.579
Hepatitis B                         0.0823      0.094      0.874      0.382      -0.102       0.267
Measles                            -0.1355      0.084     -1.620      0.105      -0.300       0.029
 BMI                                0.7170      0.095      7.567      0.000       0.531       0.903
under-five deaths                 -11.2079      0.940    -11.923      0.000     -13.051      -9.365
Polio                               0.5694      0.100      5.672      0.000       0.373       0.766
Total expenditure                   0.1694      0.079      2.158      0.031       0.015       0.323
Diphtheria                          0.6231      0.109      5.707      0.000       0.409       0.837
 HIV/AIDS                          -2.4356      0.085    -28.567      0.000      -2.603      -2.268
GDP                                 0.3915      0.174      2.244      0.025       0.049       0.734
Population                          0.1558      0.077      2.033      0.042       0.006       0.306
 thinness  1-19 years              -0.3301      0.212     -1.559      0.119      -0.745       0.085
 thinness 5-9 years                 0.0109      0.213      0.051      0.959      -0.406       0.428
Income composition of resources     1.4361      0.127     11.303      0.000       1.187       1.685
Schooling                           2.5701      0.136     18.883      0.000       2.303       2.837
==============================================================================
Omnibus:                      155.204   Durbin-Watson:                   0.682
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              593.602
Skew:                          -0.033   Prob(JB):                    1.26e-129
Kurtosis:                       5.201   Cond. No.                         45.6
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [138]:
type(y)

pandas.core.series.Series

In [139]:
df_feature_imp = pd.DataFrame()
df_feature_imp['feature'] = X.columns
df_feature_imp['importance'] = est.params.values
df_feature_imp['importance'] = df_feature_imp['importance'].abs()

In [140]:
est.params.values

array([ 6.92249317e+01,  4.80728134e-01, -2.18193675e+00,  1.10006944e+01,
        7.46124844e-02,  2.41987608e-01,  8.23464228e-02, -1.35531075e-01,
        7.17024207e-01, -1.12078704e+01,  5.69382410e-01,  1.69415725e-01,
        6.23114166e-01, -2.43557763e+00,  3.91498174e-01,  1.55813614e-01,
       -3.30137526e-01,  1.08784441e-02,  1.43606887e+00,  2.57012665e+00])

In [141]:
b_cap = np.array(b_cap)
b_cap

array([ 6.92249317e+01,  4.80728134e-01, -2.18193675e+00,  1.10006944e+01,
        7.46124844e-02,  2.41987608e-01,  8.23464228e-02, -1.35531075e-01,
        7.17024207e-01, -1.12078704e+01,  5.69382410e-01,  1.69415725e-01,
        6.23114166e-01, -2.43557763e+00,  3.91498174e-01,  1.55813614e-01,
       -3.30137526e-01,  1.08784441e-02,  1.43606887e+00,  2.57012665e+00])

In [142]:
from tqdm.auto import tqdm
itrn = 100
bh = np.zeros((itrn, X.shape[1]))
varh = np.zeros(itrn)
for i in tqdm(range(itrn)):
  eps = np.random.normal(loc = 0, scale = 1)
  y_synth = y + eps
  est=sm.OLS(y_synth,X).fit() 
  params = est.params
  bh[i] = params

  0%|          | 0/100 [00:00<?, ?it/s]

## Model Evaluation

### First we evaluate for the OLS model

In [143]:
est=sm.OLS(y, X).fit() 
y_pred = est.predict(X)

In [144]:
r2_score(y, y_pred)

0.8358157128501952

In [145]:
from sklearn.metrics import mean_squared_error

In [146]:
mean_squared_error(y, y_pred)

14.836423135880516

### ANOVA Table

In [147]:
# F - statistic = (SS-model/k)/(SS-error/n-k-1)
y = np.array(y)
y_pred = np.array(y_pred)
ss_model = sum((y_pred - y.mean())**2)
ss_error = sum((y - y_pred)**2)
ss_total = sum((y - y.mean())**2)

F_stat = (ss_model/len(pd.DataFrame(X).columns))/(ss_error/(len(X)-len(pd.DataFrame(X).columns)-1))

print("SS Model :",np.round(ss_model,2))
print("SS Error :",np.round(ss_error,2))
print("\nSS Total :",np.round(ss_total,2)," = SS Model + SS Error")
print("\nF-statistic :",np.round(F_stat,2))

SS Model : 221901.35
SS Error : 43589.41

SS Total : 265490.76  = SS Model + SS Error

F-statistic : 742.48


### Variance and Standard Deviation of the estimates for $\hat{b}$ and MSE

In [148]:
MSE = (np.sum((y-y_pred)**2))/(len(X)-len(X.columns)) # best estimator of sigma-squared

var_b = MSE*((X_trans_X_inv).diagonal())
sd_b = np.sqrt(var_b)
ts_b = b_cap / sd_b

### We now evaluate our model with Normal Equations

In [149]:
y_stat = np.matmul(X, b_cap)

In [150]:
mean_squared_error(y, y_stat)

14.836423135880517

In [151]:
r2_score(y, y_stat)

0.8358157128501952

## Check for Multicollinearity

In [153]:
df=pd.read_csv('/kaggle/input/life-expectancy-who/Life Expectancy Data.csv')

In [154]:
df.head()

Country  Year      Status  Life expectancy   Adult Mortality  \
0  Afghanistan  2015  Developing              65.0            263.0   
1  Afghanistan  2014  Developing              59.9            271.0   
2  Afghanistan  2013  Developing              59.9            268.0   
3  Afghanistan  2012  Developing              59.5            272.0   
4  Afghanistan  2011  Developing              59.2            275.0   

   infant deaths  Alcohol  percentage expenditure  Hepatitis B  Measles   ...  \
0             62     0.01               71.279624         65.0      1154  ...   
1             64     0.01               73.523582         62.0       492  ...   
2             66     0.01               73.219243         64.0       430  ...   
3             69     0.01               78.184215         67.0      2787  ...   
4             71     0.01                7.097109         68.0      3013  ...   

   Polio  Total expenditure  Diphtheria    HIV/AIDS         GDP  Population  \
0    6.0               8.16         65.0        0.1  584.259210  33736494.0   
1   58.0               8.18         62.0        0.1  612.696514    327582.0   
2   62.0               8.13         64.0        0.1  631.744976  31731688.0   
3   67.0               8.52         67.0        0.1  669.959000   3696958.0   
4   68.0               7.87         68.0        0.1   63.537231   2978599.0   

    thinness  1-19 years   thinness 5-9 years  \
0                   17.2                 17.3   
1                   17.5                 17.5   
2                   17.7                 17.7   
3                   17.9                 18.0   
4                   18.2                 18.2   

   Income composition of resources  Schooling  
0                            0.479       10.1  
1                            0.476       10.0  
2                            0.470        9.9  
3                            0.463        9.8  
4                            0.454        9.5  

[5 rows x 22 columns]

In [155]:
X_df = df.drop(['Life expectancy ', 'Year', 'Country'], axis = 1)
y_df = df['Life expectancy ']

In [157]:
X_df['Status'] = X_df['Status'].apply(lambda x: 1 if x == 'Developed' else 0)

In [158]:
cols_df = X_df.columns
X_df = StandardScaler().fit_transform(X_df)
X_df = pd.DataFrame(X_df, columns = cols_df)
X_df = sm.add_constant(X_df) 
X_df.head()

const  Status  Adult Mortality  infant deaths   Alcohol  \
0    1.0     0.0         0.790238       0.268824 -1.133571   
1    1.0     0.0         0.854614       0.285786 -1.133571   
2    1.0     0.0         0.830473       0.302749 -1.133571   
3    1.0     0.0         0.862660       0.328193 -1.133571   
4    1.0     0.0         0.886801       0.345155 -1.133571   

   percentage expenditure  Hepatitis B  Measles       BMI   \
0               -0.335570    -0.635971 -0.110384 -0.959116   
1               -0.334441    -0.755661 -0.168124 -0.984066   
2               -0.334594    -0.675868 -0.173531 -1.009015   
3               -0.332096    -0.556178  0.032045 -1.033964   
4               -0.367862    -0.516281  0.051757 -1.053924   

   under-five deaths      Polio  Total expenditure  Diphtheria    HIV/AIDS  \
0            0.255359 -3.268019           0.889486    -0.730578  -0.323445   
1            0.274060 -1.048077           0.897493    -0.857092  -0.323445   
2            0.292761 -0.877312           0.877476    -0.772749  -0.323445   
3            0.317696 -0.663856           1.033609    -0.646235  -0.323445   
4            0.342631 -0.621165           0.773387    -0.604064  -0.323445   

        GDP  Population   thinness  1-19 years   thinness 5-9 years  \
0 -0.483546    0.343993               2.796805             2.757185   
1 -0.481553   -0.203706               2.864687             2.801550   
2 -0.480218    0.311126               2.909942             2.845914   
3 -0.477539   -0.148469               2.955197             2.912461   
4 -0.520044   -0.160246               3.023079             2.956826   

   Income composition of resources  Schooling  
0                        -0.704483  -0.563614  
1                        -0.718710  -0.593391  
2                        -0.747164  -0.623168  
3                        -0.780360  -0.652944  
4                        -0.823042  -0.742275

In [160]:

X_df = X_df.replace([np.inf, -np.inf], np.nan)

# Calculate the median of each column
median = X_df.median()

# Use fillna() function to replace NaN values with the median
X_df = X_df.fillna(median)

# Now do the same for y_df
y_df = y_df.replace([np.inf, -np.inf], np.nan)
median = y_df.median()
y_df = y_df.fillna(median)


In [161]:
est1=sm.OLS(y_df,X_df).fit() 
est1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:       Life expectancy    R-squared:                       0.818
Model:                            OLS   Adj. R-squared:                  0.816
Method:                 Least Squares   F-statistic:                     727.0
Date:                Wed, 20 Sep 2023   Prob (F-statistic):               0.00
Time:                        02:48:55   Log-Likelihood:                -8285.8
No. Observations:                2938   AIC:                         1.661e+04
Df Residuals:                    2919   BIC:                         1.672e+04
Df Model:                          18                                         
Covariance Type:            nonrobust                                         
===================================================================================================
                                      coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------------------------------------------
const                              69.2771      0.077    902.588      0.000      69.127      69.428
Status                           3.592e-15   2.57e-16     13.951      0.000    3.09e-15     4.1e-15
Adult Mortality                    -2.5334      0.099    -25.676      0.000      -2.727      -2.340
infant deaths                      11.7266      1.000     11.722      0.000       9.765      13.688
Alcohol                             0.4821      0.098      4.925      0.000       0.290       0.674
percentage expenditure              0.1589      0.180      0.883      0.377      -0.194       0.512
Hepatitis B                        -0.3826      0.094     -4.086      0.000      -0.566      -0.199
Measles                            -0.2351      0.088     -2.665      0.008      -0.408      -0.062
 BMI                                0.8806      0.099      8.888      0.000       0.686       1.075
under-five deaths                 -11.9245      0.997    -11.956      0.000     -13.880      -9.969
Polio                               0.6728      0.105      6.415      0.000       0.467       0.878
Total expenditure                   0.2338      0.085      2.745      0.006       0.067       0.401
Diphtheria                          0.9544      0.111      8.628      0.000       0.738       1.171
 HIV/AIDS                          -2.3952      0.090    -26.723      0.000      -2.571      -2.219
GDP                                 0.6679      0.197      3.391      0.001       0.282       1.054
Population                         -0.0048      0.104     -0.046      0.963      -0.208       0.198
 thinness  1-19 years              -0.3738      0.224     -1.671      0.095      -0.812       0.065
 thinness 5-9 years                 0.0161      0.225      0.072      0.943      -0.425       0.457
Income composition of resources     1.2241      0.134      9.168      0.000       0.962       1.486
Schooling                           2.2568      0.140     16.079      0.000       1.982       2.532
==============================================================================
Omnibus:                      138.571   Durbin-Watson:                   0.720
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              400.632
Skew:                          -0.191   Prob(JB):                     1.01e-87
Kurtosis:                       4.768   Cond. No.                     4.71e+18
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The smallest eigenvalue is 7.02e-34. This might indicate that there are
strong multicollinearity problems or that the design matrix is singular.
"""

In [162]:
y_pred_df = est1.predict(X_df)
print('r2_score: ' + str(r2_score(y_df, y_pred_df)))
print('MSE: ' + str(mean_squared_error(y_df, y_pred_df)))

r2_score: 0.8176134490612316
MSE: 16.486374680240164


## Ridge Regression

In [163]:
ridge = Ridge()
parameters = {'alpha':[1e-4,1e-2,1,1e2,1e4]}


model = GridSearchCV(ridge, parameters, scoring = 'r2')
model.fit(X, y)

GridSearchCV(estimator=Ridge(),
             param_grid={'alpha': [0.0001, 0.01, 1, 100.0, 10000.0]},
             scoring='r2')

In [164]:
model.best_estimator_

Ridge(alpha=1)

In [165]:
ridge = Ridge(alpha = 1)
ridge.fit(X,y)

y_pred_ridge = ridge.predict(X)

r2_score(y, y_pred_ridge)

0.8357288594313401

## Lasso Regression

In [166]:
lasso = Lasso()
parameters = {'alpha':[1e-4,1e-2,1,1e2,1e4]}


model = GridSearchCV(lasso, parameters, scoring = 'r2')
model.fit(X, y)

GridSearchCV(estimator=Lasso(),
             param_grid={'alpha': [0.0001, 0.01, 1, 100.0, 10000.0]},
             scoring='r2')

In [167]:
model.best_estimator_

Lasso(alpha=0.01)

In [168]:
lasso = Lasso(alpha = 0.01)
lasso.fit(X,y)

y_pred_lasso = lasso.predict(X)

r2_score(y, y_pred_lasso)

0.835056075669443

## Residual Analysis

### Using $\hat{b}$ from Normal Equations

In [170]:
resid = y_stat - y
n1 = pd.DataFrame({'Y': y, 'Residual': resid})

In [171]:
fig=px.scatter(n1,x='Y',y='Residual',template='plotly_dark',title='<b> Reisdual Analysis for Regression using Normal Equations')
fig.add_hline(y=0)
fig.show()

### Using the model without the highly correlated features

In [172]:
resid_df = y_pred_df - y
n2 = pd.DataFrame({'Y': y, 'Residual': resid_df})

In [173]:
fig=px.scatter(n2,x='Y',y='Residual',template='plotly_dark',title='<b> Reisdual Analysis for Regression without the highly correlated features')
fig.add_hline(y=0)
fig.show()

### Using the Ridge Regression

In [174]:
resid_ridge = y_pred_ridge - y
n3 = pd.DataFrame({'Y': y, 'Residual': resid_ridge})

In [175]:
fig=px.scatter(n3,x='Y',y='Residual',template='plotly_dark',title='<b> Reisdual Analysis for Ridge Regression')
fig.add_hline(y=0)
fig.show()

In [176]:
resid_lasso = y_pred_lasso - y
n4 = pd.DataFrame({'Y': y, 'Residual': resid_lasso})

In [177]:
fig=px.scatter(n4,x='Y',y='Residual',template='plotly_dark',title='<b> Reisdual Analysis for Lasso Regression')
fig.add_hline(y=0)
fig.show()